## Importation des bibliothèques nécessaires

In [1]:
from bs4 import BeautifulSoup
import pandas as pd 
from time import sleep
import time
import pymongo
import pandas as pd
from pymongo import MongoClient
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.common.exceptions import NoSuchElementException

## Connexion a linkedin

In [2]:
def connect_to_linkedin ():
    driver.get("https://www.linkedin.com/checkpoint/lg/sign-in-another-account")
    time.sleep(5)
    username = driver.find_element_by_id("username")
    username.send_keys("gaithkrifa123@gmail.com")
    pword = driver.find_element_by_id("password")
    pword.send_keys("hedimarzouk1230")
    driver.find_element_by_xpath("//button[@type='submit']").click()

## Scrolling à la fin des pages

In [3]:
def scrolling_function ():
    SCROLL_PAUSE_TIME = 1.8
    # Get scroll height
    last_height = driver.execute_script("return document.body.scrollHeight")
    while True:
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
        time.sleep(SCROLL_PAUSE_TIME)
        new_height = driver.execute_script("return document.body.scrollHeight")
        if new_height == last_height:
            break
        last_height = new_height
    return 

## Scraper les details des posts

In [4]:
def get_posts_details(soupe):
    poste_date =[] 
    post_text = []
    post_nbreagi = []
    post_nb_comm = []
    post_nb_partage = []
    post_video_link = []
    containers =soupe.find_all('div', {'class':'occludable-update ember-view'})

    for container in containers:
        print(container)
        try:
            his=container.find('span', class_ ="visually-hidden")
    #         print(his.get_text().strip())
            poste_date.append(his.get_text().strip())
        except:
            poste_date.append('none')
        try:
            text=container.find('span', class_ ="break-words")
            post_text.append(text.get_text().strip())
            
        except:
            post_text.append('none')
        try:
            nbreagi=container.find('span', class_ ="social-details-social-counts__reactions-count")
    #         print(nbreagi.get_text().strip())
            post_nbreagi.append(nbreagi.get_text().strip())
        except:
            post_nbreagi.append('0')  
        try:       
            nb_comm=container.find('button',class_="t-black--light t-12 hoverable-link-text")
    #         print(nb_comm.get_text().strip())
            post_nb_comm.append(nb_comm.get_text().strip())
        except:
            post_nb_comm.append('0')        

        try:        
            nb_partage=container.find('li',class_="social-details-social-counts__item social-details-social-counts__item--with-social-proof")
    #         print(nb_partage.get_text().strip())
            post_nb_partage.append(nb_partage.get_text().strip())
        except:
            post_nb_partage.append('0')
    return poste_date,post_text,post_nbreagi,post_nb_comm,post_nb_partage

## Scraper le lien des posts de type image

In [5]:
def get_images_details(soupe):
    images = []
    containers =soupe.find_all('div', {'class':'occludable-update ember-view'})    
    for container in containers :
        try:
            try:
                img_link=container.find('img',class_="ivm-view-attr__img--centered feed-shared-image__image feed-shared-image__image--constrained lazy-image ember-view")                                     
                imglink= img_link['src']
                images.append(imglink)
            except:
                list_img=[]
                im=container.find_all('img',class_="ivm-view-attr__img--centered feed-shared-image__image lazy-image ember-view")
                for i in im:
                    ii=i['src']
                    list_img.append(ii)
                images.append(list_img)
  
        except:
            images.append('none')           
           
    return images

## Scraper le lien des posts de type video

In [6]:
def get_video_details(soupe):
    post_video_link = []
    containers =soupe.find_all('div', {'class':'occludable-update ember-view'})    
    for container in containers :
        try:
            video_link=container.find('video',class_="vjs-tech")
            videolink= video_link['src']
            post_video_link.append(videolink)
        except:
            post_video_link.append('none')
    return post_video_link     

## Scraper le lien des posts de type article

In [7]:
def get_Articles_details(soupe):
    articles = [] 
    containers =soupe.find_all('div', {'class':'occludable-update ember-view'})    
    for container in containers :
        try : 
            article_link = container.find("article")
            articles.append(article_link.a['href'])
        except:
            articles.append('none')
    return articles 

## Main

In [8]:
company = input("Enter your value: ")
page = "https://www.linkedin.com/company/"+company+"/"
driver = webdriver.Chrome("C:\\Users\\gaith\\OneDrive\\Bureau\\projects\\chromedriver.exe")
connect_to_linkedin ()

for i in ["articles","images","videos"]:
    try :
        driver.get(page+"posts/?feedView="+i)
        scrolling_function ()
        src =driver.page_source
        soupe =BeautifulSoup(src, 'lxml')
        data1 = get_posts_details(soupe)
        if i == 'videos':
            data2 = tuple(get_video_details(soupe))
            VideoData = pd.DataFrame(
            {'poste_date': data1[0],
             'post_text': data1[1],
             'likes': data1[2],       
             "comments":data1[3],
             "shares": data1[4],
             "post_link":data2,
             "type" : "Video",
             "competitor":company
            })
        elif i == 'articles':
            data2 = tuple(get_Articles_details(soupe))
            ArticlesData = pd.DataFrame(
            {'poste_date': data1[0],
             'post_text': data1[1],
             'likes': data1[2],       
             "comments":data1[3],
             "shares": data1[4],
             "post_link":data2,
             "type" : "Article",
             "competitor":company
            })
        elif i == 'images':
            data2 = tuple(get_images_details(soupe))
            ImagesData = pd.DataFrame(
            {'poste_date': data1[0],
             'post_text': data1[1],
             'likes': data1[2],       
             "comments":data1[3],
             "shares": data1[4],
             "post_link":data2,
             "type" : "Image",
             "competitor":company
            })

    except :
        print('we have an error')


Enter your value: talan


C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\4089112531.py:3: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("C:\\Users\\gaith\\OneDrive\\Bureau\\projects\\chromedriver.exe")
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\2523015606.py:4: DeprecationWarning: find_element_by_* commands are deprecated. Please use find_element() instead
  username = driver.find_element_by_id("username")
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\2523015606.py:6: DeprecationWarning: find_element_by_* commands are deprecated. Please use find_element() instead
  pword = driver.find_element_by_id("password")
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\2523015606.py:8: DeprecationWarning: find_element_by_* commands are deprecated. Please use find_element() instead
  driver.find_element_by_xpath("//button[@type='submit']").click()


<div class="occludable-update ember-view" id="ember60">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative feed-shared-update-v2--e2e artdeco-card ember-view" data-urn="urn:li:activity:6801065852738301954" id="ember84"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 153 abonnés Il y a 1 an" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="ZBAml8Lc5SvjS9ht7Iwpdw==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="ZBAml8Lc5SvjS9ht7Iwpdw==" data-control-name=

<div class="occludable-update ember-view" id="ember60">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative feed-shared-update-v2--e2e artdeco-card ember-view" data-urn="urn:li:activity:6942765970272731136" id="ember253"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 153 abonnés Il y a 1 semaine" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="fR9yWP3u7e2emHZS8ZCDeg==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="fR9yWP3u7e2emHZS8ZCDeg==" data-control

<div class="occludable-update ember-view" id="ember483">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative feed-shared-update-v2--e2e artdeco-card ember-view" data-urn="urn:li:activity:6865929886679273472" id="ember493"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 153 abonnés Il y a 7 mois" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="xyQpQHv5xlVScav1VrHnfQ==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="xyQpQHv5xlVScav1VrHnfQ==" data-control-n

...

<div class="occludable-update ember-view" id="ember60">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative artdeco-card ember-view" data-urn="urn:li:activity:6931946475895586819" id="ember201"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 154 abonnés Il y a 1 mois" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="i0dI8fpaLnsTif+MpAXEvw==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="i0dI8fpaLnsTif+MpAXEvw==" data-control-name="actor_picture">
<span c

<div class="occludable-update ember-view" id="ember72">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative artdeco-card ember-view" data-urn="urn:li:activity:6918117565646983168" id="ember330"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 154 abonnés Il y a 2 mois" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="f74/Vzyr1JJ83Mu0zA5ZeQ==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="f74/Vzyr1JJ83Mu0zA5ZeQ==" data-control-name="actor_picture">
<span c

<div class="occludable-update ember-view" id="ember506">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative artdeco-card ember-view" data-urn="urn:li:activity:6872589481514463232" id="ember602"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 154 abonnés Il y a 7 mois" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="ZtTa1we49MZn/mrnihfW1Q==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="ZtTa1we49MZn/mrnihfW1Q==" data-control-name="actor_picture">
<span 

<div class="occludable-update ember-view" id="ember846">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative artdeco-card ember-view" data-urn="urn:li:activity:6788820220992651264" id="ember947"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 154 abonnés Il y a 1 an" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="CtFPDq48mSF7LGQd5drzGg==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="CtFPDq48mSF7LGQd5drzGg==" data-control-name="actor_picture">
<span cl

<div class="occludable-update ember-view" id="ember1191">
<div class="feed-shared-update-v2 feed-shared-update-v2--minimal-padding full-height relative artdeco-card ember-view" data-urn="urn:li:activity:6544936867408805888" id="ember1322"><div>
<div role="status">
<!-- --> </div>
<h2 class="visually-hidden">
                Post du fil d’actualité
            </h2>
<div class="feed-shared-actor display-flex feed-shared-actor--with-control-menu">
<!-- -->
<a aria-label="Voir l’entreprise : Talan 168 154 abonnés Il y a 3 ans" class="app-aware-link feed-shared-actor__container-link relative display-flex flex-grow-1" data-control-id="apFSgzMyOGTNFCUQ11as7Q==" data-control-name="actor_container" href="https://www.linkedin.com/company/talan/?miniCompanyUrn=urn%3Ali%3Afs_miniCompany%3A28542" target="_self">
<div class="feed-shared-actor__container absolute"></div>
<div class="feed-shared-actor__image relative" data-control-id="apFSgzMyOGTNFCUQ11as7Q==" data-control-name="actor_picture">
<span

# Traitement de données

In [9]:
ImagesData

poste_date                                          post_text  \
0    Il y a 1 semaine  [AVIS D'EXPERT] La protection des données est ...   
1       Il y a 1 mois  [CAS CLIENT] Comment structurer et rationalise...   
2       Il y a 1 mois  🏆 Congrats to Ons Jabeur who becomes the first...   
3       Il y a 1 mois  🎂 𝐍𝐨𝐮𝐬 𝐬𝐨𝐦𝐦𝐞𝐬 𝐟𝐢𝐞𝐫𝐬 𝐝’𝐚𝐧𝐧𝐨𝐧𝐜𝐞𝐫 𝐪𝐮𝐞 𝐥𝐞 𝐠𝐫𝐨𝐮𝐩𝐞 𝐓...   
4       Il y a 2 mois  [WEBINAR] Nos experts Jean-Baptiste Acquaviva,...   
..                ...                                                ...   
190      Il y a 5 ans  Talan Canada Recrute ! Vous cherchez de nouvea...   
191      Il y a 5 ans  Welcome to Toronto!Talan Conseils Canada is pl...   
192      Il y a 5 ans  BIG DATA - Nous serons présents au Salon Big D...   
193      Il y a 5 ans  Come visit the Talan NY HR team at the Fordham...   
194      Il y a 5 ans  « La création de TalanConsulting conforte la c...   

    likes         comments       shares  \
0      77                0   9 partages   
1      41                0   6 partages   
2     336   5 commentaires  26 partages   
3     517  30 commentaires  19 partages   
4      39    1 commentaire   5 partages   
..    ...              ...          ...   
190    56   7 commentaires  13 partages   
191    67   3 commentaires  15 partages   
192    33    1 commentaire  16 partages   
193    20                0   5 partages   
194    67   3 commentaires  19 partages   

                                             post_link   type competitor  
0    https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
1    https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
2    https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
3    https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
4    https://media-exp1.licdn.com/dms/image/C4D22AQ...  Image      talan  
..                                                 ...    ...        ...  
190  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
191  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
192  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
193  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  
194  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image      talan  

[195 rows x 8 columns]

In [10]:
import datetime
import time
list_clean=[ImagesData,ArticlesData,VideoData]
historique=['poste_date','poste_date','poste_date']
for idx,j in enumerate(list_clean):
    for i in range(0,len(j)):
        date=j[historique[idx]][i].split()
        if 'h' in date:
            j[historique[idx]][i]=str(datetime.date.today())
        if 'heures' in date:
            j[historique[idx]][i]=str(datetime.date.today())
        if 'mois' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(30*int(nb)))
        if 'minutes' in date:
            j[historique[idx]][i]=str(datetime.date.today())
        if 'jours' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(int(nb)))
        if 'j' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(int(nb)))
        if 'jour' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(int(nb)))
        if 'semaine' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(7*int(nb)))
        if 'sem' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(7*int(nb)))
        if 'semaines' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(7*int(nb)))
        
        if 'ans' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(360*int(nb)))
        if 'an' in date:
            nb=date[3]
            j[historique[idx]][i]=str(datetime.date.today()-datetime.timedelta(360*int(nb)))

In [11]:
list_clean=[ImagesData,ArticlesData,VideoData]
historique=['poste_date','poste_date','poste_date']
for idx,j in enumerate(list_clean):
        j[historique[idx]]=j[historique[idx]].apply(lambda poste_date :datetime.datetime.strptime(poste_date,'%Y-%m-%d'))

In [12]:
import re
list_clean=[ImagesData,ArticlesData,VideoData]
historique=['shares','shares','shares']
for idx,j in enumerate(list_clean):
    for i in range(0,len(j)):
        j[historique[idx]][i]=re.sub("partages","",j[historique[idx]][i])
        j[historique[idx]][i]=re.sub("partage","",j[historique[idx]][i])
        j[historique[idx]][i]=re.sub("\xa0","",j[historique[idx]][i])
        j[historique[idx]][i]=re.sub("\u202f","",j[historique[idx]][i])

C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\627767753.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  j[historique[idx]][i]=re.sub("partages","",j[historique[idx]][i])
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\627767753.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  j[historique[idx]][i]=re.sub("partage","",j[historique[idx]][i])
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\627767753.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#retur

In [13]:
list_clean=[ImagesData,ArticlesData,VideoData]
historique=['comments','comments','comments']
for idx,j in enumerate(list_clean):
    for i in range(0,len(j)):
        j[historique[idx]][i]=re.sub("commentaires","",j[historique[idx]][i])
        j[historique[idx]][i]=re.sub("commentaire","",j[historique[idx]][i])
        j[historique[idx]][i]=re.sub("\xa0","",j[historique[idx]][i])
        j[historique[idx]][i]=re.sub("\u202f","",j[historique[idx]][i])

C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\1393698897.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  j[historique[idx]][i]=re.sub("commentaires","",j[historique[idx]][i])
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\1393698897.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  j[historique[idx]][i]=re.sub("commentaire","",j[historique[idx]][i])
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\1393698897.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

In [14]:
list_clean=[ImagesData,ArticlesData,VideoData]
historique=['likes','likes','likes']
for idx,j in enumerate(list_clean):
    for i in range(0,len(j)):
        j[historique[idx]][i]=re.sub("\xa0","",j[historique[idx]][i])
        j[historique[idx]][i]=re.sub("\u202f","",j[historique[idx]][i])

C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\3975141873.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  j[historique[idx]][i]=re.sub("\xa0","",j[historique[idx]][i])
C:\Users\gaith\AppData\Local\Temp\ipykernel_19684\3975141873.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  j[historique[idx]][i]=re.sub("\u202f","",j[historique[idx]][i])


In [15]:
result= pd.concat([ImagesData, ArticlesData,VideoData], axis=0)
result.reset_index(drop=True)

poste_date                                          post_text likes  \
0   2022-06-18  [AVIS D'EXPERT] La protection des données est ...    77   
1   2022-05-26  [CAS CLIENT] Comment structurer et rationalise...    41   
2   2022-05-26  🏆 Congrats to Ons Jabeur who becomes the first...   336   
3   2022-05-26  🎂 𝐍𝐨𝐮𝐬 𝐬𝐨𝐦𝐦𝐞𝐬 𝐟𝐢𝐞𝐫𝐬 𝐝’𝐚𝐧𝐧𝐨𝐧𝐜𝐞𝐫 𝐪𝐮𝐞 𝐥𝐞 𝐠𝐫𝐨𝐮𝐩𝐞 𝐓...   517   
4   2022-04-26  [WEBINAR] Nos experts Jean-Baptiste Acquaviva,...    39   
..         ...                                                ...   ...   
229 2019-07-11  Vous n'avez pas pu venir à Viva Technology ? R...    48   
230 2019-07-11  Pas d'intelligence artificielle sans design ! ...    44   
231 2019-07-11  Comment donner envie aux jeunes femmes de rejo...    77   
232 2019-07-11  🎈 À vous de jouer ! 🎈 Nous sommes fiers de vou...    89   
233 2019-07-11  Quelles transformations entraîne l'IA ? Jean-P...    73   

    comments shares                                          post_link   type  \
0          0      9  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image   
1          0      6  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image   
2          5     26  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image   
3         30     19  https://media-exp1.licdn.com/dms/image/C4E22AQ...  Image   
4          1      5  https://media-exp1.licdn.com/dms/image/C4D22AQ...  Image   
..       ...    ...                                                ...    ...   
229        0     13  https://dms.licdn.com/playback/C5605AQG0iXaR4q...  Video   
230        0     16  https://dms.licdn.com/playback/C4E05AQEppwqm4c...  Video   
231        1     15  https://dms.licdn.com/playback/C5605AQEzpnuniM...  Video   
232        0     35  https://dms.licdn.com/playback/C4E05AQEeKm-GE9...  Video   
233        2      7  https://dms.licdn.com/playback/C5605AQGU4poYJ2...  Video   

    competitor  
0        talan  
1        talan  
2        talan  
3        talan  
4        talan  
..         ...  
229      talan  
230      talan  
231      talan  
232      talan  
233      talan  

[234 rows x 8 columns]

In [16]:
result['likes'] = result['likes'].astype('int')
result['shares'] = result['shares'].astype('int')
result['comments'] = result['comments'].astype('int')

result

poste_date                                          post_text  likes  \
0  2022-06-18  [AVIS D'EXPERT] La protection des données est ...     77   
1  2022-05-26  [CAS CLIENT] Comment structurer et rationalise...     41   
2  2022-05-26  🏆 Congrats to Ons Jabeur who becomes the first...    336   
3  2022-05-26  🎂 𝐍𝐨𝐮𝐬 𝐬𝐨𝐦𝐦𝐞𝐬 𝐟𝐢𝐞𝐫𝐬 𝐝’𝐚𝐧𝐧𝐨𝐧𝐜𝐞𝐫 𝐪𝐮𝐞 𝐥𝐞 𝐠𝐫𝐨𝐮𝐩𝐞 𝐓...    517   
4  2022-04-26  [WEBINAR] Nos experts Jean-Baptiste Acquaviva,...     39   
..        ...                                                ...    ...   
30 2019-07-11  Vous n'avez pas pu venir à Viva Technology ? R...     48   
31 2019-07-11  Pas d'intelligence artificielle sans design ! ...     44   
32 2019-07-11  Comment donner envie aux jeunes femmes de rejo...     77   
33 2019-07-11  🎈 À vous de jouer ! 🎈 Nous sommes fiers de vou...     89   
34 2019-07-11  Quelles transformations entraîne l'IA ? Jean-P...     73   

    comments  shares                                          post_link  \
0          0       9  https://media-exp1.licdn.com/dms/image/C4E22AQ...   
1          0       6  https://media-exp1.licdn.com/dms/image/C4E22AQ...   
2          5      26  https://media-exp1.licdn.com/dms/image/C4E22AQ...   
3         30      19  https://media-exp1.licdn.com/dms/image/C4E22AQ...   
4          1       5  https://media-exp1.licdn.com/dms/image/C4D22AQ...   
..       ...     ...                                                ...   
30         0      13  https://dms.licdn.com/playback/C5605AQG0iXaR4q...   
31         0      16  https://dms.licdn.com/playback/C4E05AQEppwqm4c...   
32         1      15  https://dms.licdn.com/playback/C5605AQEzpnuniM...   
33         0      35  https://dms.licdn.com/playback/C4E05AQEeKm-GE9...   
34         2       7  https://dms.licdn.com/playback/C5605AQGU4poYJ2...   

     type competitor  
0   Image      talan  
1   Image      talan  
2   Image      talan  
3   Image      talan  
4   Image      talan  
..    ...        ...  
30  Video      talan  
31  Video      talan  
32  Video      talan  
33  Video      talan  
34  Video      talan  

[234 rows x 8 columns]

## Stockage de dataframe dans note base donnée 

In [17]:
client = MongoClient()
client = MongoClient("mongodb://localhost:27017")
db=client["myapp"]
data=result.to_dict(orient ="records")
db.LinkedinPosts.insert_many(data)